In [229]:
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader, TensorDataset
import numpy as np
import pandas as pd
from sklearn.preprocessing import StandardScaler
from scipy import stats



import seaborn as sns
from sklearn import metrics, datasets
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.model_selection import train_test_split


In [230]:
pd.reset_option('display.max_rows')
pd.set_option('display.max_columns', None)

In [231]:
df = pd.read_csv("/Users/ik/QMinersHackathon42/data/features_many.csv")
df.head() #ten elo boost pro home team je divny, jako ona si to ta neuronka asi překouše, ale jestli ji nenechat, at si to odvodi sama

orig_index  Season        Date  HID  AID market_type  y_home_win  \
0           0    1990  1990-09-21   24   16        3way           1   
1           1    1990  1990-09-21   15   18        3way           1   
2           2    1990  1990-09-21   10   22        3way           1   
3           3    1990  1990-09-21    4    5        3way           1   
4           4    1990  1990-09-21   19    0        3way           0   

   y_away_win  y_draw  oddsH  oddsA  elo_h  elo_a  elo_diff   elo_p_h  \
0           0       0   1.50   2.98    0.0    0.0      50.0  0.571463   
1           0       0   1.51   2.93    0.0    0.0      50.0  0.571463   
2           0       0   1.65   2.42    0.0    0.0      50.0  0.571463   
3           0       0   1.62   2.53    0.0    0.0      50.0  0.571463   
4           1       0   1.60   2.56    0.0    0.0      50.0  0.571463   

   pts_pg_h  pts_pg_a  gd_pg_h  gd_pg_a  games_season_h  games_season_a  \
0       0.0       0.0      0.0      0.0               0               0   
1       0.0       0.0      0.0      0.0               0               0   
2       0.0       0.0      0.0      0.0               0               0   
3       0.0       0.0      0.0      0.0               0               0   
4       0.0       0.0      0.0      0.0               0               0   

   rest_days_h  rest_days_a  rest_diff  back_to_back_h  back_to_back_a  \
0          NaN          NaN        NaN               0               0   
1          NaN          NaN        NaN               0               0   
2          NaN          NaN        NaN               0               0   
3          NaN          NaN        NaN               0               0   
4          NaN          NaN        NaN               0               0   

   home_streak_h  away_streak_a  h_gf_fast  h_ga_fast  h_gf_slow  h_ga_slow  \
0              0              0        0.0        0.0        0.0        0.0   
1              0              0        0.0        0.0        0.0        0.0   
2              0              0        0.0        0.0        0.0        0.0   
3              0              0        0.0        0.0        0.0        0.0   
4              0              0        0.0        0.0        0.0        0.0   

   h_gf_p1_fast  h_gf_p2_fast  h_gf_p3_fast  h_ga_p1_fast  h_ga_p2_fast  \
0           0.0           0.0           0.0           0.0           0.0   
1           0.0           0.0           0.0           0.0           0.0   
2           0.0           0.0           0.0           0.0           0.0   
3           0.0           0.0           0.0           0.0           0.0   
4           0.0           0.0           0.0           0.0           0.0   

   h_ga_p3_fast  h_gf_p1_share  h_gf_p2_share  h_gf_p3_share  \
0           0.0       0.333333       0.333333       0.333333   
1           0.0       0.333333       0.333333       0.333333   
2           0.0       0.333333       0.333333       0.333333   
3           0.0       0.333333       0.333333       0.333333   
4           0.0       0.333333       0.333333       0.333333   

   h_third_period_goal_diff  h_ot_rate_fast  h_ot_win_rate_fast  a_gf_fast  \
0                       0.0             0.0                 0.0        0.0   
1                       0.0             0.0                 0.0        0.0   
2                       0.0             0.0                 0.0        0.0   
3                       0.0             0.0                 0.0        0.0   
4                       0.0             0.0                 0.0        0.0   

   a_ga_fast  a_gf_slow  a_ga_slow  a_gf_p1_fast  a_gf_p2_fast  a_gf_p3_fast  \
0        0.0        0.0        0.0           0.0           0.0           0.0   
1        0.0        0.0        0.0           0.0           0.0           0.0   
2        0.0        0.0        0.0           0.0           0.0           0.0   
3        0.0        0.0        0.0           0.0           0.0           0.0   
4        0.0        0.0        0.0           0.0           0.

In [232]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7396 entries, 0 to 7395
Data columns (total 97 columns):
 #   Column                       Non-Null Count  Dtype  
---  ------                       --------------  -----  
 0   orig_index                   7396 non-null   int64  
 1   Season                       7396 non-null   int64  
 2   Date                         7396 non-null   object 
 3   HID                          7396 non-null   int64  
 4   AID                          7396 non-null   int64  
 5   market_type                  7396 non-null   object 
 6   y_home_win                   7396 non-null   int64  
 7   y_away_win                   7396 non-null   int64  
 8   y_draw                       7396 non-null   int64  
 9   oddsH                        7396 non-null   float64
 10  oddsA                        7396 non-null   float64
 11  elo_h                        7396 non-null   float64
 12  elo_a                        7396 non-null   float64
 13  elo_diff          

In [233]:
df = df[df["y_draw"] == 0]
df.head()

orig_index  Season        Date  HID  AID market_type  y_home_win  \
0           0    1990  1990-09-21   24   16        3way           1   
1           1    1990  1990-09-21   15   18        3way           1   
2           2    1990  1990-09-21   10   22        3way           1   
3           3    1990  1990-09-21    4    5        3way           1   
4           4    1990  1990-09-21   19    0        3way           0   

   y_away_win  y_draw  oddsH  oddsA  elo_h  elo_a  elo_diff   elo_p_h  \
0           0       0   1.50   2.98    0.0    0.0      50.0  0.571463   
1           0       0   1.51   2.93    0.0    0.0      50.0  0.571463   
2           0       0   1.65   2.42    0.0    0.0      50.0  0.571463   
3           0       0   1.62   2.53    0.0    0.0      50.0  0.571463   
4           1       0   1.60   2.56    0.0    0.0      50.0  0.571463   

   pts_pg_h  pts_pg_a  gd_pg_h  gd_pg_a  games_season_h  games_season_a  \
0       0.0       0.0      0.0      0.0               0               0   
1       0.0       0.0      0.0      0.0               0               0   
2       0.0       0.0      0.0      0.0               0               0   
3       0.0       0.0      0.0      0.0               0               0   
4       0.0       0.0      0.0      0.0               0               0   

   rest_days_h  rest_days_a  rest_diff  back_to_back_h  back_to_back_a  \
0          NaN          NaN        NaN               0               0   
1          NaN          NaN        NaN               0               0   
2          NaN          NaN        NaN               0               0   
3          NaN          NaN        NaN               0               0   
4          NaN          NaN        NaN               0               0   

   home_streak_h  away_streak_a  h_gf_fast  h_ga_fast  h_gf_slow  h_ga_slow  \
0              0              0        0.0        0.0        0.0        0.0   
1              0              0        0.0        0.0        0.0        0.0   
2              0              0        0.0        0.0        0.0        0.0   
3              0              0        0.0        0.0        0.0        0.0   
4              0              0        0.0        0.0        0.0        0.0   

   h_gf_p1_fast  h_gf_p2_fast  h_gf_p3_fast  h_ga_p1_fast  h_ga_p2_fast  \
0           0.0           0.0           0.0           0.0           0.0   
1           0.0           0.0           0.0           0.0           0.0   
2           0.0           0.0           0.0           0.0           0.0   
3           0.0           0.0           0.0           0.0           0.0   
4           0.0           0.0           0.0           0.0           0.0   

   h_ga_p3_fast  h_gf_p1_share  h_gf_p2_share  h_gf_p3_share  \
0           0.0       0.333333       0.333333       0.333333   
1           0.0       0.333333       0.333333       0.333333   
2           0.0       0.333333       0.333333       0.333333   
3           0.0       0.333333       0.333333       0.333333   
4           0.0       0.333333       0.333333       0.333333   

   h_third_period_goal_diff  h_ot_rate_fast  h_ot_win_rate_fast  a_gf_fast  \
0                       0.0             0.0                 0.0        0.0   
1                       0.0             0.0                 0.0        0.0   
2                       0.0             0.0                 0.0        0.0   
3                       0.0             0.0                 0.0        0.0   
4                       0.0             0.0                 0.0        0.0   

   a_ga_fast  a_gf_slow  a_ga_slow  a_gf_p1_fast  a_gf_p2_fast  a_gf_p3_fast  \
0        0.0        0.0        0.0           0.0           0.0           0.0   
1        0.0        0.0        0.0           0.0           0.0           0.0   
2        0.0        0.0        0.0           0.0           0.0           0.0   
3        0.0        0.0        0.0           0.0           0.0           0.0   
4        0.0        0.0        0.0           0.0           0.

In [234]:
df.drop(columns = ["Season", "Date", "y_draw", "elo_p_h", "market_type", "y_away_win"], inplace=True)
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 6806 entries, 0 to 7395
Data columns (total 91 columns):
 #   Column                       Non-Null Count  Dtype  
---  ------                       --------------  -----  
 0   orig_index                   6806 non-null   int64  
 1   HID                          6806 non-null   int64  
 2   AID                          6806 non-null   int64  
 3   y_home_win                   6806 non-null   int64  
 4   oddsH                        6806 non-null   float64
 5   oddsA                        6806 non-null   float64
 6   elo_h                        6806 non-null   float64
 7   elo_a                        6806 non-null   float64
 8   elo_diff                     6806 non-null   float64
 9   pts_pg_h                     6806 non-null   float64
 10  pts_pg_a                     6806 non-null   float64
 11  gd_pg_h                      6806 non-null   float64
 12  gd_pg_a                      6806 non-null   float64
 13  games_season_h         

In [235]:
df = df.replace(np.nan,0) #we can later after splitting data try mean, because now there would have been leak of info

In [236]:
df["Bookmaker_prob"] = (1/df["oddsH"])/(1/df["oddsH"]  + 1/df["oddsA"])

df.describe()

orig_index          HID          AID   y_home_win        oddsH  \
count  6806.000000  6806.000000  6806.000000  6806.000000  6806.000000   
mean   3864.283720    14.339113    14.281810     0.628563     1.536380   
std    2119.293692     7.298821     7.300675     0.483224     0.319973   
min       0.000000     0.000000     0.000000     0.000000     1.050000   
25%    2090.500000     8.000000     8.000000     0.000000     1.340000   
50%    3981.500000    16.000000    16.000000     1.000000     1.460000   
75%    5693.750000    20.000000    20.000000     1.000000     1.630000   
max    7395.000000    25.000000    25.000000     1.000000     4.700000   

             oddsA        elo_h        elo_a     elo_diff     pts_pg_h  \
count  6806.000000  6806.000000  6806.000000  6806.000000  6806.000000   
mean      2.618249     7.418290     7.351110    50.067180     0.487156   
std       0.836939    67.562998    67.642888    98.316117     0.179732   
min       1.260000  -257.922804  -260.402442  -304.506730     0.000000   
25%       2.060000   -34.395651   -34.805348   -14.001706     0.400000   
50%       2.440000     8.826831     8.364095    50.101228     0.500000   
75%       2.960000    52.279292    52.775023   113.942219     0.595238   
max       9.210000   198.946076   205.515657   410.491391     1.000000   

          pts_pg_a      gd_pg_h      gd_pg_a  games_season_h  games_season_a  \
count  6806.000000  6806.000000  6806.000000     6806.000000     6806.000000   
mean      0.493854    -0.015237     0.017452       25.035704       25.045107   
std       0.181961     0.902057     0.921246       14.822478       14.829797   
min       0.000000    -6.000000    -5.000000        0.000000        0.000000   
25%       0.400000    -0.500000    -0.500000       12.000000       12.000000   
50%       0.500000     0.000000     0.000000       25.000000       25.000000   
75%       0.600000     0.500000     0.523810       38.000000       38.000000   
max       1.000000     5.000000     6.000000       51.000000       51.000000   

       rest_days_h  rest_days_a    rest_diff  back_to_back_h  back_to_back_a  \
count  6806.000000  6806.000000  6806.000000     6806.000000     6806.000000   
mean      8.827211     6.847488     1.899647        0.018219        0.017044   
std     104.294690    27.458942    97.939133        0.133753        0.129444   
min       0.000000     0.000000  -740.000000        0.000000        0.000000   
25%       2.000000     2.000000     0.000000        0.000000        0.000000   
50%       2.000000     2.000000     0.000000        0.000000        0.000000   
75%       4.000000     4.000000     0.000000        0.000000        0.000000   
max    6394.000000   929.000000  6205.000000        1.000000        1.000000   

       home_streak_h  away_streak_a    h_gf_fast    h_ga_fast    h_gf_slow  \
count    6806.000000    6806.000000  6806.000000  6806.000000  6806.000000   
mean        0.279606       0.294152     2.778585     2.826282     2.749044   
std         0.599156       0.671352     0.698298     0.704469     0.552330   
min         0.000000       0.000000     0.000000     0.000000     0.000000   
25%         0.000000       0.000000     2.307482     2.347697     2.477219   
50%         0.000000       0.000000     2.758925     2.779116     2.780270   
75%         0.000000       0.000000     3.224786     3.270905     3.080587   
max         5.000000      10.000000     5.943915     6.034778     4.741928   

         h_ga_slow  h_gf_p1_fast  h_gf_p2_fast  h_gf_p3_fast  h_ga_p1_fast  \
count  6806.000000   6806.000000   6806.000000   6806.000000   6806.000000   
mean      2.736838      0.829146      0.958789      0.919234      0.845562   
std       0.516073      0.325511      0.358552      0.336228      0.330382   
min       0.000000      0.000000      0.000000      0.000000      0.000000   
25%       2.481112      0.601322      0.704345      0.685353      0.609095   
50%       2.755901      0.805057      0.931376      0.893761 

In [237]:
df.drop(columns = ["oddsH", "oddsA"], inplace=True)

In [238]:
data = df.drop(columns=[ "y_home_win", "Bookmaker_prob"]).values
target = df["y_home_win"].values
bookmaker_prob = df["Bookmaker_prob"].values
print(np.unique(target))

[0 1]


In [239]:
scaler = StandardScaler()

random_seed = 42

print(len(bookmaker_prob))
print(len(data))
Xtrain, Xval, ytrain, yval_data, bookmaker_prob_train, bookmaker_prob_val_data = train_test_split(
    data, target, bookmaker_prob, test_size=0.25, shuffle=False)

##
Xtrain = scaler.fit_transform(Xtrain)
Xval_data = scaler.transform(Xval)
print(Xtrain)

6806
6806
[[-1.80330578  1.24843079  0.18709103 ... -0.31796094 -0.3588332
  -1.33055234]
 [-1.80269871  0.04331349  0.45464851 ... -0.31796094 -0.3588332
  -1.33055234]
 [-1.80209165 -0.62619612  0.98976347 ... -0.31796094 -0.3588332
  -1.33055234]
 ...
 [ 1.6515051   0.44501926  0.58842725 ...  1.04490911  0.60497672
   2.08860945]
 [ 1.65211217  0.04331349 -0.6155814  ... -1.24624133 -0.30546498
   2.31655357]
 [ 1.65271923 -1.02790188  1.25732095 ...  0.51280784 -0.23274708
  -0.98863616]]


In [240]:
X_train = torch.tensor(Xtrain, dtype=torch.float32)
bookmaker_prob_train = torch.tensor(bookmaker_prob_train, dtype=torch.float32).unsqueeze(1)
y_train = torch.tensor(ytrain, dtype=torch.float32).unsqueeze(1)



train_dataset = TensorDataset(X_train, bookmaker_prob_train, y_train)
train_loader = DataLoader(train_dataset, batch_size=64, shuffle=False) #do not shuffle because time series data

In [241]:
import torch.nn.functional as F

class ProbabilityEstimatorNN(nn.Module):
    def __init__(self, input_dim, hidden_dim=64):
        super().__init__()
        self.fc1 = nn.Linear(input_dim, hidden_dim)
        self.fc2 = nn.Linear(hidden_dim, hidden_dim)
        self.output = nn.Linear(hidden_dim, 1)  # Single output neuron

    # Xavier/Glorot initialization for hidden layers
        nn.init.xavier_uniform_(self.fc1.weight)
        nn.init.xavier_uniform_(self.fc2.weight)
        nn.init.zeros_(self.fc1.bias)
        nn.init.zeros_(self.fc2.bias)
        
        # Small random init for output layer
        nn.init.uniform_(self.output.weight, -0.1, 0.1)
        nn.init.zeros_(self.output.bias)

    def forward(self, x):
        x = F.relu(self.fc1(x))
        x = F.relu(self.fc2(x))
        x = self.output(x)  # Outputs probabilities in [0,1]
        return x

import torch

def decorrelation_loss(outputs, bookmaker_prob, lambda_decorr):
    outputs = outputs.view(-1)
    bookmaker_prob = bookmaker_prob.view(-1)
    cov = torch.mean((outputs - outputs.mean()) * (bookmaker_prob - bookmaker_prob.mean()))
    loss = lambda_decorr * cov**2
    return loss


def l2_regularization(model, lambda_):
    # Sum of squared weights (L2 norm), excluding biases
    l2_norm = sum(
        torch.sum(param ** 2) 
        for param in model.parameters() 
        if param.requires_grad and param.dim() > 1
    )
    return lambda_ * l2_norm
# in training loop:
# outputs = model(X_batch)
# loss = criterion(outputs, y_batch)
# reg = l2_regularization(model, lambda_)
# total_loss = loss + reg
# total_loss.backward()



In [ ]:
# Suppose X_train, y_train, bookmaker_probs_train are your training data tensors
# X_train: (num_samples, feature_dim), y_train: (num_samples, 1), bookmaker_probs_train: (num_samples,)
# Wrap in Dataset and DataLoader
feature_dim = data.shape[1]
model = ProbabilityEstimatorNN(feature_dim)
optimizer = torch.optim.Adam(model.parameters(), lr=0.001)


criterion = nn.BCEWithLogitsLoss()

num_samples_train = X_train.shape[0]


# Initialize model, optimizer


# Hyperparameters for loss

lambda_ = 0.01
lambda_decorr = 0.3
epochs = 100


# Training loop
def train(model, optimizer, criterion, num_samples_train, lambda_decorr, epochs, train_loader, lambda_):
    
    for epoch in range(epochs):
        total_loss = 0
        for X_batch, bookmaker_batch, y_batch in train_loader:
            optimizer.zero_grad()
            outputs = model(X_batch) 
            #print("outputs min/max:", outputs.min().item(), outputs.max().item()) #debugging
            loss = criterion(outputs, y_batch) + decorrelation_loss(bookmaker_batch, outputs,lambda_decorr) + l2_regularization(model, lambda_)
            loss.backward() 
            for name, param in model.named_parameters():
                if param.grad is not None:
                    print(name, param.grad.norm().item())          
             # Backpropagation
            optimizer.step()           # Update parameters)
            total_loss += loss.item() * X_batch.size(0)
        avg_loss = total_loss / len(train_loader.dataset)


    return avg_loss

avg = train(model, optimizer, criterion, num_samples_train, lambda_decorr, epochs, train_loader, lambda_)


print(avg)

outputs min/max: -1.6136480569839478 -0.004944939166307449
fc1.weight 0.7398234605789185
fc1.bias 0.06689798086881638
fc2.weight 0.8276476860046387
fc2.bias 0.10524250566959381
output.weight 2.021089792251587
output.bias 0.3787428140640259
outputs min/max: -0.4199242889881134 0.19448815286159515
fc1.weight 0.22709040343761444
fc1.bias 0.02418500930070877
fc2.weight 0.24130165576934814
fc2.bias 0.04697522148489952
output.weight 0.4104407727718353
output.bias 0.18880942463874817
outputs min/max: -0.46977195143699646 0.1425783932209015
fc1.weight 0.21303847432136536
fc1.bias 0.02256575971841812
fc2.weight 0.21875634789466858
fc2.bias 0.04206744208931923
output.weight 0.36741816997528076
output.bias 0.16591313481330872
outputs min/max: -0.49617743492126465 0.1792144924402237
fc1.weight 0.2092285454273224
fc1.bias 0.014257929287850857
fc2.weight 0.19329483807086945
fc2.bias 0.021799923852086067
output.weight 0.19761499762535095
output.bias 0.059177763760089874
outputs min/max: -0.3191120028

In [243]:
X_val = torch.tensor(Xval_data, dtype=torch.float32)
bookmaker_prob_val = torch.tensor(bookmaker_prob_val_data, dtype=torch.float32).unsqueeze(1)
y_val = torch.tensor(yval_data, dtype=torch.float32).unsqueeze(1)

val_dataset = TensorDataset(X_val, bookmaker_prob_val, y_val)
val_loader = DataLoader(val_dataset, batch_size=64, shuffle=False)

In [244]:
num_samples_val = X_val.shape[0]

def predict(model, criterion, val_loader):
    all_predictions = []
    num_samples = 0
    total_loss = 0
    with torch.no_grad():
        for X_batch, y_batch, bookmaker_batch in val_loader:
            outputs = model(X_batch)
            loss = criterion(outputs, y_batch) #- (1/num_samples_val)*decorrel_weight*decorellation(bookmaker_batch, outputs)
            batch_size = X_batch.size(0)
            total_loss += loss.item() * batch_size
            num_samples += batch_size
            probs = torch.sigmoid(outputs).view(-1).cpu()
            all_predictions.append(probs)

    avg_loss = total_loss / num_samples
    #print(f"Validation Loss: {avg_loss:.4f}")
    flat_array = torch.cat(all_predictions).numpy()
    mse = mean_squared_error(yval_data, flat_array)
    r2 = r2_score(yval_data, flat_array)

    #print("MSE:", mse)
    #print("R2:", r2)
    return avg_loss, flat_array, mse, r2


##should flatten array of tensors

"""for item in all_predictions:
    item = torch.flatten(item)
concatenated = torch.cat(all_predictions)
flat_array = concatenated.numpy()"""
# Proper flattening when appending
# Do NOT flatten after the loop, flatten DURING append


# concatenate correctly







'for item in all_predictions:\n    item = torch.flatten(item)\nconcatenated = torch.cat(all_predictions)\nflat_array = concatenated.numpy()'

In [245]:
def accuracy(flat_array, sensitivity):
    adjusted = np.full_like(flat_array, 0.5)  # Initialize with 0.5

    mask_high = flat_array > (0.5 + sensitivity)
    mask_low = flat_array < (0.5 - sensitivity)

    adjusted[mask_high] = 1
    adjusted[mask_low] = 0

    adjusted = adjusted.reshape(-1)

    acc = (adjusted == yval_data).mean()
    print(f"Validation accuracy of normalized model: {acc:.4f}")
    print(np.unique(yval_data))  
    print("acc on making a guess:", acc*len(flat_array)/np.sum(flat_array != 0.5))
    return acc

In [246]:
avg_loss, flat_array, mse, r2 = predict(model, criterion, val_loader)
print(flat_array)
print(accuracy(flat_array, 0.03 ))
print("average loss:", avg_loss, "mse:", mse, "r2:", r2)

[0.6529804  0.61074466 0.599998   ... 0.563566   0.6074297  0.6122266 ]
Validation accuracy of normalized model: 0.5817
[0 1]
acc on making a guess: 0.581668625146886
0.581668625146886
average loss: 0.6613328068152718 mse: 0.231053426861763 r2: 0.028895258903503418


In [247]:


# Hyperparameters for loss
lambda_decorr = 0.3
lambda_ = 0.3
acc_coeff = 0.03
avg_train_loss_set = []
val_loss_set = []
array_for_outcomes = np.array([])
mse_arr = []
r2_arr = []
x_axis = []
acc = []
 # Training loop

for hundred in range(15):
    ffeature_dim = data.shape[1]
    model = ProbabilityEstimatorNN(feature_dim)
    optimizer = torch.optim.Adam(model.parameters(), lr=0.001)
    criterion = nn.BCEWithLogitsLoss()

    num_samples_train = X_train.shape[0]
    epochs = 100
    print(hundred)
    avg_train_loss_set.append(train(model, optimizer, criterion, num_samples_train, lambda_decorr, epochs, train_loader, lambda_))

    print(avg_train_loss_set)
    val_loss, flat_array, mse, r2 = predict(model, criterion, val_loader)
    val_loss_set.append(val_loss)
    #array_for_outcomes = np.vstack([flat_array, array_for_outcomes])
    mse_arr.append(mse)
    r2_arr.append(r2)
    x_axis.append(hundred)
    acc.append(accuracy(flat_array, acc_coeff))
    



    

0
outputs min/max: -1.2647300958633423 0.0010056394385173917
fc1.weight 5.226133823394775
fc1.bias 0.05628981813788414
fc2.weight 4.808855056762695
fc2.bias 0.09115000814199448
output.weight 1.9684474468231201
output.bias 0.353570818901062
outputs min/max: -0.5074084997177124 -0.06237566098570824
fc1.weight 5.149837970733643
fc1.bias 0.03316778689622879
fc2.weight 4.727076053619385
fc2.bias 0.05619872733950615
output.weight 0.7260595560073853
output.bias 0.21803569793701172
outputs min/max: -0.42463040351867676 -0.06484787166118622
fc1.weight 5.1070332527160645
fc1.bias 0.023455016314983368
fc2.weight 4.687711715698242
fc2.bias 0.044468481093645096
output.weight 0.5834215879440308
output.bias 0.19146299362182617
outputs min/max: -0.7133915424346924 0.2783516049385071
fc1.weight 5.066843509674072
fc1.bias 0.013852348551154137
fc2.weight 4.652161598205566
fc2.bias 0.023380933329463005
output.weight 0.4073832631111145
output.bias 0.07908259332180023
outputs min/max: -0.6578037738800049 0.

KeyboardInterrupt: 

In [ ]:
import matplotlib
import matplotlib.pyplot as plt
%matplotlib inline
x_axis = [1,2,3,4,5,6,7,8,9,10,11,12,13,14,15]
x_axis = [x * 100 for x in x_axis]
print(x_axis)
plt.figure(figsize=(20,6))
plt.plot(x_axis, avg_train_loss_set,'or-') #o: body, r: barva, -: spojení bodů linkou
plt.plot(x_axis, val_loss_set,'ob-')
plt.plot(x_axis, mse_arr,'oy-')
plt.plot(x_axis, r2_arr,'ok-')
plt.xlabel('epochs')
plt.ylabel('accuracy')
plt.legend(['train loss', 'validation loss', 'MSE', 'R2'])

In [ ]:
import matplotlib
import matplotlib.pyplot as plt
%matplotlib inline

plt.figure(figsize=(20,6))

plt.plot(x_axis, acc,'og-')

plt.xlabel('epochs')
plt.ylabel('accuracy')
plt.legend(["accuracy"])

In [ ]:

epochs = 1000
avg_train_loss_set = []
val_loss_set = []
array_for_outcomes = np.array([])
mse_arr = []
r2_arr = []
x_axis = []
acc = []
 # Training loop

for dw in range(10):
    decorrel_weight = dw*0.1
    feature_dim = data.shape[1]
    model = ProbabilityEstimatorNN(feature_dim)
    optimizer = torch.optim.SGD(model.parameters(), lr=0.01)
    criterion = nn.BCEWithLogitsLoss()
    num_samples_train = X_train.shape[0]
    print(epochs)
    avg_train_loss_set.append(train(model, optimizer, criterion, num_samples_train, decorrel_weight, epochs, train_loader, lambda_))

    val_loss, flat_array, mse, r2 = predict(model, criterion, val_loader)
    val_loss_set.append(val_loss)
    #array_for_outcomes = np.vstack([flat_array, array_for_outcomes])
    mse_arr.append(mse)
    r2_arr.append(r2)
    x_axis.append(dw*0.1)
    acc.append(accuracy(flat_array, lambda_))

In [ ]:
x_axis = [0.0, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
plt.figure(figsize=(20,6))
plt.plot(x_axis, avg_train_loss_set,'or-') #o: body, r: barva, -: spojení bodů linkou
plt.plot(x_axis, val_loss_set,'ob-')
plt.plot(x_axis, mse_arr,'oy-')
plt.plot(x_axis, r2_arr,'ok-')
plt.xlabel('corr_coeff')
plt.ylabel('accuracy')
plt.legend(['train loss', 'validation loss', 'MSE', 'R2'])

plt.figure(figsize=(20,6))

plt.plot(x_axis, acc,'og-')

plt.xlabel('corr_coeff')
plt.ylabel('accuracy')
plt.legend(["accuracy"])

In [ ]:

epochs = 1000
avg_train_loss_set = []
val_loss_set = []
array_for_outcomes = np.array([])
mse_arr = []
r2_arr = []
x_axis = []
acc = []
 # Training loop


feature_dim = data.shape[1]
model = ProbabilityEstimatorNN(feature_dim)
optimizer = torch.optim.SGD(model.parameters(), lr=0.01)
criterion = nn.BCELoss()
num_samples_train = X_train.shape[0]
avg_train_loss_set.append(train(model, optimizer, criterion, num_samples_train, 0.2, epochs, train_loader))

val_loss, flat_array, mse, r2 = predict(model, criterion, val_loader)
print(flat_array)
val_loss_set.append(val_loss)
#array_for_outcomes = np.vstack([flat_array, array_for_outcomes])
mse_arr.append(mse)
r2_arr.append(r2)
for sensitivity in range(10):
    sens = sensitivity*0.03
    x_axis.append(sensitivity*0.03)
    acc.append(accuracy(flat_array, sens))

In [ ]:


plt.figure(figsize=(20,6))

plt.plot(x_axis, acc,'og-')

plt.xlabel('corr_coeff')
plt.ylabel('accuracy')
plt.legend(["accuracy"])